# Load dataset

In [1]:
#Acknowlegement: Some codes used to initialise BERT are from BERT tutorial(https://colab.research.google.com/drive/1Y4o3jh3ZH70tl6mCd76vz_IxX23biCPP)

In [1]:
# Import necessary libraries
import re
import string
import os 
from collections import defaultdict
from collections import Counter
import time
import numpy as np
import torch
import datetime
import copy
from transformers import get_linear_schedule_with_warmup
from transformers import BertForSequenceClassification, AdamW, BertConfig
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from covid_tools import *
from BERTs import *

ModuleNotFoundError: No module named 'spacy'

In [7]:
! pip install scipy

In [2]:
with open('./Pythonbooks/Data/COVID/b_label1.json') as f:
    labels_b_1 = json.load(f)

with open('./Pythonbooks/Data/COVID/b_label2a.json') as f:
    labels_b_2a = json.load(f)

with open('./Pythonbooks/Data/COVID/b_label3.json') as f:
    labels_b_3 = json.load(f)

with open('./Pythonbooks/Data/COVID/b_label4.json') as f:
    labels_b_4 = json.load(f)

with open('./Pythonbooks/Data/COVID/b_label5.json') as f:
    labels_b_5 = json.load(f)

with open('./Pythonbooks/Data/COVID/b_label2b.json') as f:
    labels_b_2b = json.load(f)

NameError: name 'json' is not defined

In [24]:

# labels11 = pd.DataFrame(labels1['events'][0]['tweets'][:])
# labels12 = pd.DataFrame(labels1['events'][1]['tweets'][:])
# labels13 = pd.DataFrame(labels1['events'][2]['tweets'][:])

labels21 = pd.DataFrame(labels_b_2a['events'][10]['tweets'][:])
labels22 = pd.DataFrame(labels_b_2a['events'][11]['tweets'][:])

labels31 = pd.DataFrame(labels_b_3['events'][7]['tweets'][:])
labels32 = pd.DataFrame(labels_b_3['events'][8]['tweets'][:])
labels33 = pd.DataFrame(labels_b_3['events'][12]['tweets'][:])
labels34 = pd.DataFrame(labels_b_3['events'][13]['tweets'][:])
# labels32 = pd.DataFrame(labels3['events'][2]['tweets'][:])

labels41 = pd.DataFrame(labels_b_4['events'][2]['tweets'][:])
labels42 = pd.DataFrame(labels_b_4['events'][3]['tweets'][:])
labels43 = pd.DataFrame(labels_b_4['events'][4]['tweets'][:])

labels51 = pd.DataFrame(labels_b_5['events'][8]['tweets'][:])
labels52 = pd.DataFrame(labels_b_5['events'][9]['tweets'][:])
labels53 = pd.DataFrame(labels_b_5['events'][10]['tweets'][:])
labels54 = pd.DataFrame(labels_b_5['events'][11]['tweets'][:])
labels55 = pd.DataFrame(labels_b_5['events'][12]['tweets'][:])
labels56 = pd.DataFrame(labels_b_5['events'][13]['tweets'][:])
labels57 = pd.DataFrame(labels_b_5['events'][17]['tweets'][:])
labels58 = pd.DataFrame(labels_b_5['events'][18]['tweets'][:])



# Union them all into one dataFrame
temp = [labels21, labels22, labels31, labels32, labels33, labels34, labels41, labels42, labels43, labels51,
          labels52, labels53, labels54, labels55, labels56, labels57, labels58]
all_labels_b = pd.concat(temp)
all_labels_b = all_labels_b.rename(columns={'postID': 'id'})
all_labels_b = all_labels_b.astype({"id": np.int64})
all_labels_b.reset_index()

index                   id                timestamp  \
0         0  1284639584303878145  2 Dec 2020 19:18:21 GMT   
1         1  1282135471624159234  2 Dec 2020 16:25:32 GMT   
2         2  1284923732830547968  2 Dec 2020 19:24:54 GMT   
3         3  1286831260908871681  2 Dec 2020 20:28:04 GMT   
4         4  1285847416357322752  2 Dec 2020 19:54:31 GMT   
...     ...                  ...                      ...   
7561    443  1289942323745271808  6 Dec 2020 20:01:20 GMT   
7562    444  1286273699478413312  5 Dec 2020 18:07:55 GMT   
7563    445  1292785443122094080  6 Dec 2020 20:25:13 GMT   
7564    446  1283503272461049856  5 Dec 2020 17:45:18 GMT   
7565    447  1290145839755665408  6 Dec 2020 20:03:23 GMT   

                                             categories indicatorTerms  \
0     [ThirdPartyObservation, Location, MultimediaSh...             []   
1                                          [Irrelevant]             []   
2     [FirstPartyObservation, Location, Hashtags, Ad...             []   
3     [ThirdPartyObservation, Weather, Location, Mul...             []   
4     [ThirdPartyObservation, Location, MultimediaSh...             []   
...                                                 ...            ...   
7561  [ThirdPartyObservation, Location, MultimediaSh...             []   
7562  [ThirdPartyObservation, Location, MultimediaSh...             []   
7563  [ThirdPartyObservation, MultimediaShare, Conte...             []   
7564  [ThirdPartyObservation, Location, MultimediaSh...             []   
7565  [ThirdPartyObservation, Location, MultimediaSh...             []   

     priority                                               text  
0         Low  Mayor of Houston canceled Texas Republican Con...  
1         Low  Georgia hospital live status:\nWellStar Cobb -...  
2         Low  Pls wear a mask to restaurants ??? #Houston #h...  
3      Medium  I hope Houston dodges bad weather, but glad to...  
4        High  Beijing Says US Ordered it to Close Chinese Co...  
...       ...                                                ...  
7561      Low  Should N.J. start a border war and grab income...  
7562      Low  NYC Says It Has Prevented More Than 5k Potenti...  
7563      Low  What Happens to Viral Particles on the Subway ...  
7564      Low  ?? Jamal Crawford is out of quarantine and fin...  
7565      Low  @BradfordJSmith1 @WHO New York, Pennsylvania, ...  

[7566 rows x 7 columns]

In [25]:
all_labels_union_b = []
# For debugging
count = 0
# Iterate all tweets including duplicate labels
for id in all_labels_b.id.values:
    priority = []
    categories = []
    count += 1
    print(count)
    # concatenate all labels for information type and prioritization task
    for idx in range(len(all_labels_b)):
      if id == all_labels_b.iloc[idx].id:
        priority += [all_labels_b.iloc[idx].priority]
        categories += all_labels_b.iloc[idx].categories

#     print(list(set(priority)))
    all_labels_union_b.append({'id': id,'full_text':all_labels_b.iloc[idx].text, 'priority': list(set(priority)), 'categories': list(set(categories))})
# Transer list to dataFrame
all_labels_union_b = pd.DataFrame(all_labels_union_b)
all_labels_union_b.to_csv('cache/all_labeled_duplicated_b.csv')
all_labels_union_b.drop_duplicates('id', keep='first', inplace=True)
all_labels_union_b.to_csv('cache/all_labeled_b.csv')

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [26]:
frame = all_labels_union_b.copy()

In [27]:
frame.index = np.arange(len(frame))
categories = ['Low', 'Medium', 'High', 'Critical']
for idx in range(len(frame)):
    length = len(frame.loc[idx, 'priority'])
    final_label = None
    print(idx)

    if length >= 3:
        number_count = [0, 0, 0, 0]
        for priority_label in frame.loc[idx, 'priority']:
            if priority_label == 'Low':
                number_count[0] += 1
            elif priority_label == 'Medium':
                number_count[1] += 1
            elif priority_label == 'High':
                number_count[2] += 1
            else:
                number_count[3] += 1
        final_label = categories[np.argmax(np.array(number_count))]
    else:
        final_label = frame.loc[idx, 'priority'][0]
        # print(final_label)
        frame.loc[idx, 'priority'] = final_label
        
cv19_b_run_labeled = frame

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [28]:
cv19_b_run_labeled

id                                          full_text  \
0     1284639584303878145  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
1     1282135471624159234  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
2     1284923732830547968  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
3     1286831260908871681  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
4     1285847416357322752  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
...                   ...                                                ...   
7095  1277244473882402828  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7096  1279897731046268928  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7097  1272112852380389377  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7098  1271539463882264580  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7099  1280959202085736450  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   

     priority                                         categories  
0         Low  [Sentiment, ThirdPartyObservation, Location, M...  
1         Low                                       [Irrelevant]  
2         Low  [FirstPartyObservation, Hashtags, Location, Ad...  
3      Medium  [Hashtags, Sentiment, MultimediaShare, Locatio...  
4        High  [ThirdPartyObservation, News, Location, Multim...  
...       ...                                                ...  
7095      Low  [Sentiment, MultimediaShare, Location, ThirdPa...  
7096      Low  [ThirdPartyObservation, ContextualInformation,...  
7097      Low  [MultimediaShare, Advice, Location, ThirdParty...  
7098      Low  [Sentiment, MultimediaShare, Location, Discuss...  
7099      Low  [News, MultimediaShare, Location, ThirdPartyOb...  

[7100 rows x 4 columns]

## Read dataset from files

In [31]:
test = pd.read_csv('./priority/b_run/dataset_all.csv',converters={"priority": lambda x: x.strip("[]").replace("'", "").split(", "),
                                       "categories": lambda x: x.strip("[]").replace("'", "").split(", ")})


In [32]:
test

id                                          full_text  \
0     1284639584303878145  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
1     1282135471624159234  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
2     1284923732830547968  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
3     1286831260908871681  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
4     1285847416357322752  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
...                   ...                                                ...   
7095  1277244473882402828  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7096  1279897731046268928  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7097  1272112852380389377  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7098  1271539463882264580  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7099  1280959202085736450  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   

      priority                                         categories  
0        [Low]  [Sentiment, ThirdPartyObservation, Location, M...  
1        [Low]                                       [Irrelevant]  
2        [Low]  [FirstPartyObservation, Hashtags, Location, Ad...  
3     [Medium]  [Hashtags, Sentiment, MultimediaShare, Locatio...  
4       [High]  [ThirdPartyObservation, News, Location, Multim...  
...        ...                                                ...  
7095     [Low]  [Sentiment, MultimediaShare, Location, ThirdPa...  
7096     [Low]  [ThirdPartyObservation, ContextualInformation,...  
7097     [Low]  [MultimediaShare, Advice, Location, ThirdParty...  
7098     [Low]  [Sentiment, MultimediaShare, Location, Discuss...  
7099     [Low]  [News, MultimediaShare, Location, ThirdPartyOb...  

[7100 rows x 4 columns]

In [20]:
cv19_b_run_labeled = pd.read_csv('./priority/b_run/dataset_all.csv',converters={"priority": lambda x: x.strip("[]").replace("'", "").split(", "),
                                       "categories": lambda x: x.strip("[]").replace("'", "").split(", ")})


In [85]:
cv19_b_run_labeled

id                                          full_text  \
0     1284639584303878145  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
1     1282135471624159234  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
2     1284923732830547968  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
3     1286831260908871681  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
4     1285847416357322752  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
...                   ...                                                ...   
7095  1277244473882402828  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7096  1279897731046268928  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7097  1272112852380389377  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7098  1271539463882264580  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   
7099  1280959202085736450  @BradfordJSmith1 @WHO New York, Pennsylvania, ...   

     priority                                         categories  
0         Low  [Sentiment, ThirdPartyObservation, Location, M...  
1         Low                                       [Irrelevant]  
2         Low  [FirstPartyObservation, Hashtags, Location, Ad...  
3      Medium  [Hashtags, Sentiment, MultimediaShare, Locatio...  
4        High  [ThirdPartyObservation, News, Location, Multim...  
...       ...                                                ...  
7095      Low  [Sentiment, MultimediaShare, Location, ThirdPa...  
7096      Low  [ThirdPartyObservation, ContextualInformation,...  
7097      Low  [MultimediaShare, Advice, Location, ThirdParty...  
7098      Low  [Sentiment, MultimediaShare, Location, Discuss...  
7099      Low  [News, MultimediaShare, Location, ThirdPartyOb...  

[7100 rows x 4 columns]

In [104]:
cv19_b_run_labeled[['id','priority','categories']].to_csv('priority/'+'b_run'+'/dataset_all.csv',
                   index=False)

### Load TERC-IS 2020-A data

In [35]:
# load orginal data(COVID-19 TREC-IS 2020 task) from json file.
import json
import pandas as pd
cv19_dc = pd.read_json('./Pythonbooks/Data/COVID/cv19_dc_test.json',lines=True,orient='records')
cv19_ws = pd.read_json('./Pythonbooks/Data/COVID/cv19_washington_state_test.json',lines=True,orient='records')
cv19_ny = pd.read_json('./Pythonbooks/Data/COVID/cv19_nyc_test.json',lines=True,orient='records')

# Read lablled tweets from json file which contains all labels based on union of labels from all human assessors.
all_labels  = read_union_labels_from_file()

# Merge original dataset with lablled dataset based on id of tweets
cv19_dc_labeled = pd.merge(cv19_dc,all_labels,on=['id'])
cv19_ws_labeled = pd.merge(cv19_ws,all_labels,on=['id'])
cv19_ny_labeled = pd.merge(cv19_ny,all_labels,on=['id'])

# As for priorization task, we use majority vote of labels instead of union.
'''More specifically, if one tweet is assessed by more than two assessors,
 we use the most common label as the priority label. And if one tweet is assessed by less than two assessors, 
 we randomly choose one label as the true label. 
 '''
cv19_dc_labeled = extract_majority_vote_label(cv19_dc_labeled)
cv19_ny_labeled = extract_majority_vote_label(cv19_ny_labeled)
cv19_ws_labeled = extract_majority_vote_label(cv19_ws_labeled)


In [36]:
# Union them all into one dataFrame
temp = [cv19_dc_labeled,cv19_ny_labeled,cv19_ws_labeled ]
cv19_a_run_labeled =  pd.concat(temp)


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  This is separate from the ipykernel package so we can avoid doing imports until


In [112]:
def build_trainingset(trainSet):
  # Extract training set
  featureList = ['id','full_text','entities','favorite_count'] #,'favorited'
  trainF = extract_features(trainSet,featureList)

  labelList = ['priority']
  trainL_temp = extract_features(trainSet,labelList)['priority']
  trainF = extract_hashtags(trainF)
  
  trainL = []
  for label in trainL_temp:
    if label == 'Low':
      trainL.append(0)
    elif label == 'Medium':
      trainL.append(1)
    elif label == 'High':
      trainL.append(2)
    elif label == 'Critical':
      trainL.append(3)
  return trainF, trainL

In [113]:
def store_csv(df,location,val_ratio=0.2):
    trainF, trainL = build_trainingset(df)
    
    idx = np.arange(df.shape[0])
    np.random.shuffle(idx)
    
    val_size = int(len(idx) * val_ratio)
    if not os.path.exists('priority/'+location):
        os.makedirs('priority/'+location)
    
    print(len(trainL))
    df = pd.DataFrame(trainF)
    df['target'] = trainL
    df[['id','full_text','hashtags','favorite_count','categories', 'target']].to_csv('priority/'+location+'/dataset_all.csv',
                   index=False)
    
    
    
    # df_tmp = df.iloc[idx[val_size:]
    # df_test = df.iloc[idx[:val_size]
    df.iloc[idx[val_size:], :][['full_text','hashtags','favorite_count','target']].to_csv('priority/'+location+'/dataset_test.csv',
                   index=False)
                      
    df.iloc[idx[val_size:], :][['full_text','hashtags','favorite_count','target']].to_csv(
        'priority/'+location+'/dataset_train.csv',index=False)
    
    # df.iloc[idx[:val_size], :][['full_text','entities','favorite_count', target]].to_csv(
    #     'cache/dataset_val.csv', index=False
    # )
    


In [13]:
# Store training,  test set into csv file
if not os.path.exists('/priority/'):
  store_csv(cv19_ws_labeled,location='WS') 
  store_csv(cv19_dc_labeled,location='DC') 
  store_csv(cv19_ny_labeled,location='NY')
  store_csv(cv19_a_run_labeled,location='a_run')
  store_csv(cv19_b_run_labeled,location='b_run')

2577
2504
2502
7583


KeyError: 'entities'

### Load TERC-IS 2020-B data

In [105]:
cv19_b_run_labeled = pd.read_csv('priority/b_run/dataset_all.csv')

In [106]:
# load orginal data(COVID-19 TREC-IS 2020 B task) from json file.
import json
import pandas as pd
cv19_Houston_2020 = pd.read_json('./Pythonbooks/Data/COVID/cv_Houston_2020.json',lines=True,orient='records')
cv19_Atlanta_2020 = pd.read_json('./Pythonbooks/Data/COVID/cv_Atlanta_2020.json',lines=True,orient='records')
cv19_Melbourne2020 = pd.read_json('./Pythonbooks/Data/COVID/cv_Melbourne_2020.json',lines=True,orient='records')
cv19_NYC_2020 = pd.read_json('./Pythonbooks/Data/COVID/cv_NYC_2020.json',lines=True,orient='records')
cv19_acksonville_2020 = pd.read_json('./Pythonbooks/Data/COVID/cv_Jacksonville_2020.json',lines=True,orient='records')

# Merge original dataset with lablled dataset based on id of tweets
cv19_Houston_2020_labeled = pd.merge(cv19_Houston_2020, cv19_b_run_labeled,on=['id'])
cv19_Atlanta_2020_labeled = pd.merge(cv19_Atlanta_2020, cv19_b_run_labeled,on=['id'])
cv19_Melbourne2020_labeled = pd.merge(cv19_Melbourne2020, cv19_b_run_labeled,on=['id'])
cv19_NYC_2020_labeled = pd.merge(cv19_NYC_2020, cv19_b_run_labeled, on=['id'])
cv19_acksonville_2020_labeled = pd.merge(cv19_acksonville_2020,cv19_b_run_labeled, on=['id'])


# # As for priorization task, we use majority vote of labels instead of union.

# cv19_dc_labeled = extract_majority_vote_label(cv19_dc_labeled)
# cv19_ny_labeled = extract_majority_vote_label(cv19_ny_labeled)
# cv19_ws_labeled = extract_majority_vote_label(cv19_ws_labeled)


In [111]:
cv19_Houston_2020_labeled.id

0      1289520616568102912
1      1283562734823579650
2      1284612124275335170
3      1288867135658160129
4      1284190653375643648
              ...         
967    1293215015244267520
968    1282056653689376768
969    1289750677267329024
970    1283234148874948609
971    1282330879411597312
Name: id, Length: 972, dtype: int64

In [108]:
# cat all
temp = [cv19_Houston_2020_labeled,cv19_Atlanta_2020_labeled,cv19_Melbourne2020_labeled,cv19_NYC_2020_labeled, cv19_acksonville_2020_labeled ]
cv19_b_run_labeled =  pd.concat(temp)


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  This is separate from the ipykernel package so we can avoid doing imports until


In [115]:
if not os.path.exists('/priority/'):
  store_csv(cv19_Houston_2020_labeled,location='Houston_2020') 
  store_csv(cv19_Atlanta_2020_labeled,location='Atlanta_2020') 
  store_csv(cv19_Melbourne2020_labeled,location='Melbourne2020')
  store_csv(cv19_NYC_2020_labeled,location='NYC_2020') 
  store_csv(cv19_acksonville_2020_labeled,location='acksonville_2020')
  store_csv(cv19_b_run_labeled,location='b_run')

972
976
960
954
669
4531


In [8]:
# check GPU situation
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Select the Runtime → "Change runtime type" menu to enable a GPU accelerator, ')
  print('and then re-execute this cell.')
else:
  print(gpu_info)

Wed Feb 24 05:02:07 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 450.80.02    Driver Version: 450.80.02    CUDA Version: 11.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  GeForce RTX 208...  Off  | 00000000:B2:00.0 Off |                  N/A |
| 27%   28C    P8     1W / 250W |      0MiB / 11019MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

# Pre-processing data set



In [ ]:
!pip install transformers

     |████████████████████████████████| 778kB 3.3MB/s eta 0:00:01
     |████████████████████████████████| 665kB 15.0MB/s eta 0:00:01
     |████████████████████████████████| 3.0MB 9.4MB/s eta 0:00:01
     |████████████████████████████████| 890kB 10.8MB/s eta 0:00:01
     |████████████████████████████████| 1.1MB 11.1MB/s eta 0:00:01
     |████████████████████████████████| 92kB 17.1MB/s eta 0:00:01
  Created wheel for sacremoses: filename=sacremoses-0.0.43-cp36-none-any.whl size=893260 sha256=bcbfd05d2b4b1597fe5d7207a7dd700ef2d65a2737f8f4c543f25d2dc356fcf5
  Stored in directory: /root/.cache/pip/wheels/29/3c/fd/7ce5c3f0666dab31a50123635e6fb5e19ceb42ce38d4e58f45
Successfully built sacremoses
You should consider upgrading via the 'pip install --upgrade pip' command.


## Tokenization: Bert tokenizer

In [14]:
from transformers import BertTokenizer

# Load the BERT tokenizer.
print('Loading BERT tokenizer...')
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased', do_lower_case=True)

I1216 09:45:46.435996 140181434603328 driver.py:124] Generating grammar tables from /usr/lib/python3.6/lib2to3/Grammar.txt
I1216 09:45:46.450255 140181434603328 driver.py:124] Generating grammar tables from /usr/lib/python3.6/lib2to3/PatternGrammar.txt


Loading BERT tokenizer...


In [1]:
import pandas as pd
dataset_inputs_A_run = pd.read_csv('priority/a_run/dataset_all.csv')
dataset_inputs_B_run = pd.read_csv('priority/b_run/dataset_all.csv')

In [2]:
dataset_inputs_B_run

id                                          full_text  \
0     1289520616568102912  Texas-78/1 4:36 Daily-Total 438293, Up 10064, ...   
1     1283562734823579650  Texas counties are requesting refrigerated tru...   
2     1284612124275335170  Latest health update: link in profile. @ Houst...   
3     1288867135658160129  HTV Houston Television - COVID-19 Talk with Lo...   
4     1284190653375643648  All Masks, Disinfectant Wipes/Sprays &amp; San...   
...                   ...                                                ...   
4526  1282161443488567297  The commissioner for St. Johns County just sou...   
4527  1290462720358318080  Updated: Emergency vehicles in Duval County on...   
4528  1296437616427110400  Jacksonville #Jaguars ativou o RB Ryquell Arms...   
4529  1291196194199408641  Prayers for Lt.Cunningham's family &amp; his c...   
4530  1295508708814970889  Alexander Bernardo, 22yo Dietary Aide, Park Ri...   

                                               hashtags  favorite_count  \
0      Houston Covid Covid19 medtwitter harriscounty...               0   
1                                                                     0   
2                                                                     0   
3                                                                     0   
4                                                                     0   
...                                                 ...             ...   
4526                                             Karma                4   
4527                                                                  0   
4528                             Jaguars NFL NFLBrasil                2   
4529                                                                 11   
4530                covid19 healthcareheroes WearAMask              150   

      target  
0          0  
1          1  
2          0  
3          2  
4          0  
...      ...  
4526       0  
4527       0  
4528       0  
4529       0  
4530       0  

[4531 rows x 5 columns]

In [3]:
sentences_A_run = dataset_inputs_A_run.full_text.values
labels_A_run = dataset_inputs_A_run.target.values
sentences_B_run = dataset_inputs_B_run.full_text.values
labels_B_run = dataset_inputs_B_run.target.values

In [4]:
for idx in range(len(sentences_A_run)):
  sentences_A_run[idx] = sentences_A_run[idx]  + ' '+ dataset_inputs_A_run.hashtags.values[idx] + ' ' + str(dataset_inputs_A_run.favorite_count.values[idx])

for idx in range(len(sentences_B_run)):
  sentences_B_run[idx] = sentences_B_run[idx]  + ' '+ dataset_inputs_B_run.hashtags.values[idx] + ' ' + str(dataset_inputs_B_run.favorite_count.values[idx])


In [15]:
# Print the original sentence.
print(' Original: ', sentences_A_run[0])

# Print the sentence split into tokens.
print('Tokenized: ', tokenizer.tokenize(sentences_A_run[0]))

# Print the sentence mapped to token ids.
print('Token IDs: ', tokenizer.convert_tokens_to_ids(tokenizer.tokenize(sentences_A_run[0])))

 Original:  EPA suspends enforcement of environmental laws amid coronavirus https://t.co/QyV6ysx5nx https://t.co/83zhB1xnhT   26
Tokenized:  ['epa', 'suspend', '##s', 'enforcement', 'of', 'environmental', 'laws', 'amid', 'corona', '##virus', 'https', ':', '/', '/', 't', '.', 'co', '/', 'q', '##y', '##v', '##6', '##ys', '##x', '##5', '##nx', 'https', ':', '/', '/', 't', '.', 'co', '/', '83', '##zh', '##b', '##1', '##x', '##nh', '##t', '26']
Token IDs:  [19044, 28324, 2015, 7285, 1997, 4483, 4277, 13463, 21887, 23350, 16770, 1024, 1013, 1013, 1056, 1012, 2522, 1013, 1053, 2100, 2615, 2575, 7274, 2595, 2629, 26807, 16770, 1024, 1013, 1013, 1056, 1012, 2522, 1013, 6640, 27922, 2497, 2487, 2595, 25311, 2102, 2656]


In [16]:
def Encode_sents(sentences):
    input_ids = []
    # For every sentence...
    for sent in sentences:
        # `encode` will:
        #   (1) Tokenize the sentence.
        #   (2) Prepend the `[CLS]` token to the start.
        #   (3) Append the `[SEP]` token to the end.
        #   (4) Map tokens to their IDs.
        encoded_sent = tokenizer.encode(
                            sent,                      # Sentence to encode.
                            add_special_tokens = True, # Add '[CLS]' and '[SEP]'


                            #max_length = 128,          # Truncate all sentences.
                            #return_tensors = 'pt',     # Return pytorch tensors.
                       )

        # Add the encoded sentence to the list.
        # If the length of token is over the bert limitation, cut off the back
        if(len(encoded_sent)>144):
            diff = int((len(encoded_sent) - 145)/2)
            encoded_sent = encoded_sent[diff:144+diff]
        input_ids.append(encoded_sent)
    return input_ids



In [17]:
# Tokenize all of the sentences and map the tokens to thier word IDs.
input_ids_A_run = Encode_sents(sentences_A_run)
input_ids_B_run = Encode_sents(sentences_B_run)



In [18]:
print('Max sentence length: ', max([len(sen) for sen in input_ids_A_run]))

Max sentence length:  144


## Padding


In [19]:

# We'll borrow the `pad_sequences` utility function to do this.
from keras.preprocessing.sequence import pad_sequences

# Set the maximum sequence length.

MAX_LEN = 144

print('\nPadding/truncating all sentences to %d values...' % MAX_LEN)

print('\nPadding token: "{:}", ID: {:}'.format(tokenizer.pad_token, tokenizer.pad_token_id))

# Pad our input tokens with value 0.
# "post" indicates that we want to pad and truncate at the end of the sequence,
# as opposed to the beginning.
input_ids_A_run = pad_sequences(input_ids_A_run, maxlen=MAX_LEN, dtype="long", 
                          value=0, truncating="post", padding="post")

input_ids_B_run = pad_sequences(input_ids_B_run, maxlen=MAX_LEN, dtype="long", 
                          value=0, truncating="post", padding="post")
print('\nDone.')


Padding/truncating all sentences to 144 values...

Padding token: "[PAD]", ID: 0

Done.


## Attension mask

In [20]:
# Create attention masks
def build_attension_mask(input_ids):
    attention_masks = []
    # For each sentence...
    for sent in input_ids:

        # Create the attention mask.
        #   - If a token ID is 0, then it's padding, set the mask to 0.
        #   - If a token ID is > 0, then it's a real token, set the mask to 1.
        att_mask = [int(token_id > 0) for token_id in sent]

        # Store the attention mask for this sentence.
        attention_masks.append(att_mask)
    return attention_masks


In [21]:
attention_masks_A_run = build_attension_mask(input_ids_A_run)
attention_masks_B_run = build_attension_mask(input_ids_B_run)


## Training & Validation Split



In [22]:
def BERT_cross_vali_split(input_ids, labels, attention_masks):
    # Use train_test_split to split our data into train and validation and test sets for
    # training
    from sklearn.model_selection import train_test_split

    # Use 80% for training and 20% for validation and  5% for testing.
    temp_inputs, test_inputs,  temp_labels, test_labels = train_test_split(input_ids, labels, test_size=0.05,random_state=2020)
    train_inputs, validation_inputs, train_labels, validation_labels = train_test_split(temp_inputs, temp_labels, test_size=0.2,random_state=2020)

    # Do the same for the masks.
    temp_masks, test_masks, temp_labels, _ = train_test_split(attention_masks, labels, test_size=0.05,random_state=2020)

    train_masks, validation_masks, _, _ = train_test_split(temp_masks, temp_labels, test_size=0.2,random_state=2020)
    return train_inputs,  train_labels, train_masks, validation_inputs, validation_labels, validation_masks, test_inputs, test_labels, test_masks 

In [23]:
train_inputs_A_run,  train_labels_A_run, train_masks_A_run, validation_inputs_A_run, validation_labels_A_run, validation_masks_A_run,test_inputs_A_run, test_labels_A_run, test_masks_A_run = BERT_cross_vali_split(input_ids_A_run, labels_A_run, attention_masks_A_run)

train_inputs_B_run,  train_labels_B_run, train_masks_B_run, validation_inputs_B_run, validation_labels_B_run, validation_masks_B_run,test_inputs_B_run, test_labels_B_run, test_masks_B_run = BERT_cross_vali_split(input_ids_B_run, labels_B_run, attention_masks_B_run)

In [28]:
# build the test batch
batch_A_run = [input_ids_A_run, labels_A_run, attention_masks_A_run]
batch_B_run = [input_ids_B_run, labels_B_run, attention_masks_B_run]
test_batch_A_run = [test_inputs_A_run,test_labels_A_run,test_masks_A_run]
test_batch_B_run = [test_inputs_B_run,test_labels_B_run,test_masks_B_run]

# Conduct the fine-tuning


In [24]:
categories = {0:'Low',1:'Medium',2:'High',3:'Critical'}

## Search the best hyperparameters

In [13]:
from collections import defaultdict
all_metrics_search = defaultdict()
for batch_size in [16]: #16,
  for lr in [5e-5,3e-5,2e-5]:
    print('Currently processing %s'%(str(batch_size) + '_' + str(lr)))
    Bert = Bertnn(train_inputs,train_labels,train_masks, validation_inputs,validation_labels,validation_masks,testbatch,batch_size=batch_size,lr=lr)
    all_metrics_one = Bert.searchUpsample(14)
    filename = str(batch_size) + '_' + str(lr)
    all_metrics_search[name] = all_metrics_one
    
    # store result into file
    with open(filename,'w') as file_obj:
      json.dump(all_metrics_one,file_obj)
      print('Successfully save file %s'%(filename))
    del Bert

Currently processing 16_5e-05


NameError: name 'Bertnn' is not defined

In [ ]:
all_metrics_search

defaultdict(None,
            {'16_5e-05': {0: defaultdict(None,
                          {'train_loss_values': [0.5641749259829522,
                            0.5641749259829522,
                            0.5090744014829397,
                            0.5090744014829397,
                            0.3772193490900099,
                            0.3772193490900099,
                            0.24945555636659264,
                            0.24945555636659264],
                           'train_acc_all': [0.84, 0.85375, 0.890625, 0.9325],
                           'train_precision_all': [{0: 0.8405416666666667,
                             1: 0.0,
                             2: 0.0,
                             3: 0.0},
                            {0: 0.8588214285714286, 1: 0.0, 2: 0.1075, 3: 0.0},
                            {0: 0.9147370684870684,
                             1: 0.0,
                             2: 0.533047619047619,
                             3: 0.0},
   

## Incremental rectified training

In [17]:
import json
batch_size = 16
lr = 5e-5
Bert_train_A_run = Bertnn_rectified_priorization(train_inputs_A_run,train_labels_A_run,train_masks_A_run,
                                                 validation_inputs_A_run,validation_labels_A_run,
                                             validation_masks_A_run,batch_size=batch_size,test_batch=test_batch,lr=lr)
all_metrics_one_A_run = Bert.searchUpsample(110)


# del Bert_A_run
# torch.cuda.empty_cache() 

There are 1 GPU(s) available.
We will use the GPU: TITAN RTX


Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

Current increase 0 times
Current is processing category 1
Before up-sample, there are 5762 samples
There are 119 sampled in this category.
After up-sample, there are 5762 samples

Current is processing category 2
Before up-sample, there are 5762 samples
There are 277 sampled in this category.
After up-sample, there are 5762 samples

Current is processing category 3
Before up-sample, there are 5762 samples
There are 21 sampled in this category.
After up-sample, there are 5762 samples

Currrent is processing on categorie Low

Before up-sample, the ratio of current category and all samples
5345
0.9276292953835473

After up-sample, the ratio of current category and all samples
5345
0.9276292953835473

Currrent is processing on categorie Medium

Before up-sample, the ratio of current category and all samples
119
0.020652551197500868

After up-sample, the ratio of current category and all samples
119
0.020652551197500868

Currrent is processing on categorie High

Before up-sample, the ratio 

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

There are 1 GPU(s) available.
We will use the GPU: TITAN RTX

======== Epoch 1 / 4 ========
Training...
Invoke 2
Invoke 2
Invoke 2
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 1
Invoke 2
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 3
Invoke 2
Invoke 3
Invoke 2
Invoke 2
Invoke 2
Invoke 2
Invoke 2
Invoke 3
Invoke 2
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 1
Invoke 2
Invoke 2
Invoke 2
Invoke 1
Invoke 2
  Batch    40  of    361.    Elapsed: 0:00:12.
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 2
Invoke 2
Invoke 1
Invoke 1
Invoke 2
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 2
Invoke 2
Invoke 2
Invoke 2
Invoke 2
Invoke 2
Invoke 1
Invoke 1
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
  Batch    80  of    361.    Elapsed: 0:00:24.
Invoke 1
Invoke 2
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 2
Invoke 1
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
I

...

There are 1 GPU(s) available.
We will use the GPU: TITAN RTX

======== Epoch 1 / 4 ========
Training...
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invok

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

There are 1 GPU(s) available.
We will use the GPU: TITAN RTX

======== Epoch 1 / 4 ========
Training...
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invok

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

There are 1 GPU(s) available.
We will use the GPU: TITAN RTX

======== Epoch 1 / 4 ========
Training...
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
Invoke 1
Invoke 2
Invoke 3
Invoke 1
Invoke 2
  Batch    40 

### Train on 2020-A and validate on 202-B

In [63]:
BERT_train_on_A  = BertForSequenceClassification.from_pretrained(
      "bert-base-uncased",  # Use the 12-layer BERT model, with an uncased vocab.
      num_labels=4,  # The number of output labels--2 for binary classification.
      # You can increase this for multi-class tasks.
      output_attentions=False,  # Whether the model returns attentions weights.
      output_hidden_states=False,  # Whether the model returns all hidden-states.
    )
    # send model to GPU

BERT_train_on_A.load_state_dict(torch.load('./Best_val_Bert_rectified_priorization.pth'))

BERT_train_on_A.cuda()
metrics_test_on_B_dataset = BERT_train_on_A.evluate_methods.evalTest(self, self.model, batch_B_run, 4)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

<All keys matched successfully>

In [61]:
BERT_train_on_A.cuda()
metrics_test_on_B_dataset = BERT_train_on_A.evluate_methods.evalTest(self, self.model, batch_B_run, 4)

NameError: name 'BERT' is not defined

In [84]:
test_inputs = torch.tensor(batch_B_run[0]).to(torch.int64)
test_labels = torch.tensor(batch_B_run[1]).to(torch.int64)
test_masks = torch.tensor(batch_B_run[2]).to(torch.int64)
test_data = TensorDataset(test_inputs, test_masks, test_labels)
sampler = RandomSampler(test_data)
test_dataloader = DataLoader(test_data, sampler=sampler, batch_size=16)
category_number = 4
# ========================================
#               Testing
# ========================================
print()
print('Testing...')
# record the start time
t0 = time.time()

# Identify GPU to use
if torch.cuda.is_available():
    device = torch.device("cuda")
    print('There are %d GPU(s) available.' % torch.cuda.device_count())
    print('We will use the GPU:', torch.cuda.get_device_name(0))
else:
    print('No GPU available, using the CPU instead.')
    device = torch.device("cpu")
# put model in evaluation model
BERT_train_on_A.eval()

BERT_train_on_A.to(device)
# Build list to store metrics of each epoches
test_acc_all = []
test_precision_all = []
test_recall_all = []
test_f1_all = []
test_accuracy = 0
nb_test_steps, nb_test_examples = 0, 0

# Build the dict for each metrics and store metrics for each category
test_precision, test_recall, test_f1 = {}, {}, {}
for i in range(category_number):
    test_f1[i], test_precision[i], test_recall[i] = 0, 0, 0

# For each batch of training data...
for batch in test_dataloader:
    # Add batch to GPU
    batch = tuple(t.to(device) for t in batch)

    # Unpack the inputs from our dataloader
    b_input_ids, b_input_mask, b_labels = batch

    # Telling the model not to compute or store gradients, saving memory and
    # speeding up validation
    with torch.no_grad():

      outputs = BERT_train_on_A(b_input_ids, token_type_ids=None, attention_mask=b_input_mask)
      # Get the "logits" output by the model. The "logits" are the output
      # values prior to applying an activation function like the softmax.
      logits = outputs[0]

      # Move logits and labels to CPU
      logits = logits.detach().cpu().numpy()
      label_ids = b_labels.to('cpu').numpy()

      # Calculate the accuracy for this batch of test sentences.
      tmp_test_accuracy = Scoring_nn.flat_accuracy(None, logits, label_ids)

      tmp_test_precision = {}
      tmp_test_recall = {}
      tmp_test_f1 = {}
      for i in range(category_number):
        tmp_test_precision[i] = 0
        tmp_test_recall[i] = 0
        tmp_test_f1[i] = 0

      for k in range(category_number):
        tmp_test_precision[k], tmp_test_recall[k], tmp_test_f1[k] = Scoring_nn.flat_metrics(None, logits, label_ids, k)

      # Accumulate the total accuracy.
      test_accuracy += tmp_test_accuracy

      for k in range(category_number):
        test_precision[k] += tmp_test_precision[k]
        test_recall[k] += tmp_test_recall[k]
        test_f1[k] += tmp_test_f1[k]

      # Track the number of batches
      nb_test_steps += 1

# Report the final accuracy for this validation run.
print("  Accuracy: {0:.2f}".format(test_accuracy / nb_test_steps))

# Calculate the average value for each metrics
precision_avg, recall_avg, f1_avg = 0, 0, 0
for k in range(category_number):
    print("Category: %d" % (k))
    test_precision[k] = test_precision[k] / nb_test_steps
    precision_avg += test_precision[k]
    test_recall[k] = test_recall[k] / nb_test_steps
    recall_avg += test_recall[k]
    test_f1[k] = test_f1[k] / nb_test_steps
    f1_avg += test_f1[k]
    print("  Precision: {0:.4f}".format(test_precision[k]))
    print("  Recall: {0:.4f}".format(test_recall[k]))
    print("  F1: {0:.4f}".format(test_f1[k]))
# Report other metrics
print("The average precision is: {0:.4f}".format(precision_avg / category_number))
print("The average recall is: {0:.4f}".format(recall_avg / category_number))
print("The average f1 is: {0:.4f}".format(f1_avg / category_number))
print("  Testing took: {:}".format(Scoring_nn.format_time(None, time.time() - t0)))



Testing...
There are 1 GPU(s) available.
We will use the GPU: TITAN RTX
  Accuracy: 0.78
Category: 0
  Precision: 0.7815
  Recall: 1.0000
  F1: 0.8740
Category: 1
  Precision: 0.0000
  Recall: 0.0000
  F1: 0.0000
Category: 2
  Precision: 0.0000
  Recall: 0.0000
  F1: 0.0000
Category: 3
  Precision: 0.0000
  Recall: 0.0000
  F1: 0.0000
The average precision is: 0.1954
The average recall is: 0.2500
The average f1 is: 0.2185
  Testing took: 0:00:26


### Train on 2020-B and validate on 2020-A

In [ ]:
import json
batch_size = 16
lr = 5e-5
BERT_train_on_B = Bertnn_rectified_priorization(train_inputs_B_run,train_labels_B_run,train_masks_B_run, validation_inputs_B_run,
                                                validation_labels_B_run,validation_masks_B_run,
                                                batch_size=batch_size,test_batch=test_batch_B_run,lr=lr)
all_metrics_one_B = BERT_train_on_B.searchUpsample(110)


# del BERT_train_on_B
# torch.cuda.empty_cache() 

There are 1 GPU(s) available.
We will use the GPU: TITAN RTX


Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

Current increase 0 times
Current is processing category 1
Before up-sample, there are 3443 samples
There are 538 sampled in this category.
After up-sample, there are 3443 samples

Current is processing category 2
Before up-sample, there are 3443 samples
There are 251 sampled in this category.
After up-sample, there are 3443 samples

Current is processing category 3
Before up-sample, there are 3443 samples
There are 4 sampled in this category.
After up-sample, there are 3443 samples

Currrent is processing on categorie Low

Before up-sample, the ratio of current category and all samples
2650
0.7696776067383096

After up-sample, the ratio of current category and all samples
2650
0.7696776067383096

Currrent is processing on categorie Medium

Before up-sample, the ratio of current category and all samples
538
0.15625907638687192

After up-sample, the ratio of current category and all samples
538
0.15625907638687192

Currrent is processing on categorie High

Before up-sample, the ratio of 

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

There are 1 GPU(s) available.
We will use the GPU: TITAN RTX

======== Epoch 1 / 4 ========
Training...
  Batch    40  of    216.    Elapsed: 0:00:16.
  Batch    80  of    216.    Elapsed: 0:00:31.
  Batch   120  of    216.    Elapsed: 0:00:46.
  Batch   160  of    216.    Elapsed: 0:01:02.
  Batch   200  of    216.    Elapsed: 0:01:17.

  Average training loss: 2.88
  Accuracy: 0.76
Category: 0
  Precision: 0.80
  Recall: 0.95
  F1: 0.86
Category: 1
  Precision: 0.12
  Recall: 0.08
  F1: 0.08
Category: 2
  Precision: 0.16
  Recall: 0.16
  F1: 0.14
Category: 3
  Precision: 0.00
  Recall: 0.00
  F1: 0.00
The average precision is: 0.2700
The average recall is: 0.2985
The average f1 is: 0.2730
  Training epcoh took: 0:01:22

Running Validation...
  Accuracy: 0.77
Category: 0
  Precision: 0.8732
  Recall: 0.9047
  F1: 0.8839
Category: 1
  Precision: 0.2685
  Recall: 0.1355
  F1: 0.1716
Category: 2
  Precision: 0.2813
  Recall: 0.4154
  F1: 0.2967
Category: 3
  Precision: 0.0000
  Recall: 0

...

There are 1 GPU(s) available.
We will use the GPU: TITAN RTX

======== Epoch 1 / 4 ========
Training...
  Batch    40  of  1,703.    Elapsed: 0:00:18.
  Batch    80  of  1,703.    Elapsed: 0:00:36.
  Batch   120  of  1,703.    Elapsed: 0:00:54.
  Batch   160  of  1,703.    Elapsed: 0:01:12.
  Batch   200  of  1,703.    Elapsed: 0:01:30.
  Batch   240  of  1,703.    Elapsed: 0:01:48.
  Batch   280  of  1,703.    Elapsed: 0:02:06.
  Batch   320  of  1,703.    Elapsed: 0:02:24.
  Batch   360  of  1,703.    Elapsed: 0:02:42.
  Batch   400  of  1,703.    Elapsed: 0:03:00.
  Batch   440  of  1,703.    Elapsed: 0:03:18.
  Batch   480  of  1,703.    Elapsed: 0:03:36.
  Batch   520  of  1,703.    Elapsed: 0:03:53.
  Batch   560  of  1,703.    Elapsed: 0:04:11.
  Batch   600  of  1,703.    Elapsed: 0:04:29.
  Batch   640  of  1,703.    Elapsed: 0:04:47.
  Batch   680  of  1,703.    Elapsed: 0:05:05.
  Batch   720  of  1,703.    Elapsed: 0:05:23.
  Batch   760  of  1,703.    Elapsed: 0:05:40.
  B

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

There are 1 GPU(s) available.
We will use the GPU: TITAN RTX

======== Epoch 1 / 4 ========
Training...
  Batch    40  of  2,198.    Elapsed: 0:00:18.
  Batch    80  of  2,198.    Elapsed: 0:00:36.
  Batch   120  of  2,198.    Elapsed: 0:00:54.
  Batch   160  of  2,198.    Elapsed: 0:01:12.
  Batch   200  of  2,198.    Elapsed: 0:01:29.
  Batch   240  of  2,198.    Elapsed: 0:01:47.
  Batch   280  of  2,198.    Elapsed: 0:02:05.
  Batch   320  of  2,198.    Elapsed: 0:02:23.
  Batch   360  of  2,198.    Elapsed: 0:02:41.
  Batch   400  of  2,198.    Elapsed: 0:02:59.
  Batch   440  of  2,198.    Elapsed: 0:03:16.
  Batch   480  of  2,198.    Elapsed: 0:03:34.
  Batch   520  of  2,198.    Elapsed: 0:03:52.
  Batch   560  of  2,198.    Elapsed: 0:04:10.
  Batch   600  of  2,198.    Elapsed: 0:04:27.
  Batch   640  of  2,198.    Elapsed: 0:04:45.
  Batch   680  of  2,198.    Elapsed: 0:05:03.
  Batch   720  of  2,198.    Elapsed: 0:05:21.
  Batch   760  of  2,198.    Elapsed: 0:05:38.
  B

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

There are 1 GPU(s) available.
We will use the GPU: TITAN RTX

======== Epoch 1 / 4 ========
Training...
  Batch    40  of  2,694.    Elapsed: 0:00:20.
  Batch    80  of  2,694.    Elapsed: 0:00:39.
  Batch   120  of  2,694.    Elapsed: 0:00:58.
  Batch   160  of  2,694.    Elapsed: 0:01:17.
  Batch   200  of  2,694.    Elapsed: 0:01:36.
  Batch   240  of  2,694.    Elapsed: 0:01:55.
  Batch   280  of  2,694.    Elapsed: 0:02:15.
  Batch   320  of  2,694.    Elapsed: 0:02:33.
  Batch   360  of  2,694.    Elapsed: 0:02:53.
  Batch   400  of  2,694.    Elapsed: 0:03:12.
  Batch   440  of  2,694.    Elapsed: 0:03:31.
  Batch   480  of  2,694.    Elapsed: 0:03:50.
  Batch   520  of  2,694.    Elapsed: 0:04:09.
  Batch   560  of  2,694.    Elapsed: 0:04:28.
  Batch   600  of  2,694.    Elapsed: 0:04:47.
  Batch   640  of  2,694.    Elapsed: 0:05:06.
  Batch   680  of  2,694.    Elapsed: 0:05:25.
  Batch   720  of  2,694.    Elapsed: 0:05:44.
  Batch   760  of  2,694.    Elapsed: 0:06:03.
  B

In [33]:
BERT_train_on_B  = BertForSequenceClassification.from_pretrained(
      "bert-base-uncased",  # Use the 12-layer BERT model, with an uncased vocab.
      num_labels=4,  # The number of output labels--2 for binary classification.
      # You can increase this for multi-class tasks.
      output_attentions=False,  # Whether the model returns attentions weights.
      output_hidden_states=False,  # Whether the model returns all hidden-states.
    )
    # send model to GPU

BERT_train_on_B.load_state_dict(torch.load('./Best_val_Bert_rectified_priorization.pth'))

BERT_train_on_B.cuda()


Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, element

In [32]:
test_inputs = torch.tensor(batch_A_run[0]).to(torch.int64)
test_labels = torch.tensor(batch_A_run[1]).to(torch.int64)
test_masks = torch.tensor(batch_A_run[2]).to(torch.int64)
test_data = TensorDataset(test_inputs, test_masks, test_labels)
sampler = RandomSampler(test_data)
test_dataloader = DataLoader(test_data, sampler=sampler, batch_size=16)
category_number = 4

In [34]:

# ========================================
#               Testing
# ========================================
print()
print('Testing...')
# record the start time
t0 = time.time()

# Identify GPU to use
if torch.cuda.is_available():
    device = torch.device("cuda")
    print('There are %d GPU(s) available.' % torch.cuda.device_count())
    print('We will use the GPU:', torch.cuda.get_device_name(0))
else:
    print('No GPU available, using the CPU instead.')
    device = torch.device("cpu")
# put model in evaluation model
BERT_train_on_B.eval()

BERT_train_on_B.to(device)
# Build list to store metrics of each epoches
test_acc_all = []
test_precision_all = []
test_recall_all = []
test_f1_all = []
test_accuracy = 0
nb_test_steps, nb_test_examples = 0, 0

# Build the dict for each metrics and store metrics for each category
test_precision, test_recall, test_f1 = {}, {}, {}
for i in range(category_number):
    test_f1[i], test_precision[i], test_recall[i] = 0, 0, 0

# For each batch of training data...
for batch in test_dataloader:
    # Add batch to GPU
    batch = tuple(t.to(device) for t in batch)

    # Unpack the inputs from our dataloader
    b_input_ids, b_input_mask, b_labels = batch

    # Telling the model not to compute or store gradients, saving memory and
    # speeding up validation
    with torch.no_grad():

      outputs = BERT_train_on_B(b_input_ids, token_type_ids=None, attention_mask=b_input_mask)
      # Get the "logits" output by the model. The "logits" are the output
      # values prior to applying an activation function like the softmax.
      logits = outputs[0]

      # Move logits and labels to CPU
      logits = logits.detach().cpu().numpy()
      label_ids = b_labels.to('cpu').numpy()

      # Calculate the accuracy for this batch of test sentences.
      tmp_test_accuracy = Scoring_nn.flat_accuracy(None, logits, label_ids)

      tmp_test_precision = {}
      tmp_test_recall = {}
      tmp_test_f1 = {}
      for i in range(category_number):
        tmp_test_precision[i] = 0
        tmp_test_recall[i] = 0
        tmp_test_f1[i] = 0

      for k in range(category_number):
        tmp_test_precision[k], tmp_test_recall[k], tmp_test_f1[k] = Scoring_nn.flat_metrics(None, logits, label_ids, k)

      # Accumulate the total accuracy.
      test_accuracy += tmp_test_accuracy

      for k in range(category_number):
        test_precision[k] += tmp_test_precision[k]
        test_recall[k] += tmp_test_recall[k]
        test_f1[k] += tmp_test_f1[k]

      # Track the number of batches
      nb_test_steps += 1

# Report the final accuracy for this validation run.
print("  Accuracy: {0:.2f}".format(test_accuracy / nb_test_steps))

# Calculate the average value for each metrics
precision_avg, recall_avg, f1_avg = 0, 0, 0
for k in range(category_number):
    print("Category: %d" % (k))
    test_precision[k] = test_precision[k] / nb_test_steps
    precision_avg += test_precision[k]
    test_recall[k] = test_recall[k] / nb_test_steps
    recall_avg += test_recall[k]
    test_f1[k] = test_f1[k] / nb_test_steps
    f1_avg += test_f1[k]
    print("  Precision: {0:.4f}".format(test_precision[k]))
    print("  Recall: {0:.4f}".format(test_recall[k]))
    print("  F1: {0:.4f}".format(test_f1[k]))
# Report other metrics
print("The average precision is: {0:.4f}".format(precision_avg / category_number))
print("The average recall is: {0:.4f}".format(recall_avg / category_number))
print("The average f1 is: {0:.4f}".format(f1_avg / category_number))
print("  Testing took: {:}".format(Scoring_nn.format_time(None, time.time() - t0)))



Testing...
There are 1 GPU(s) available.
We will use the GPU: TITAN RTX
  Accuracy: 0.77
Category: 0
  Precision: 0.9341
  Recall: 0.8204
  F1: 0.8689
Category: 1
  Precision: 0.0098
  Recall: 0.0137
  F1: 0.0105
Category: 2
  Precision: 0.0605
  Recall: 0.1057
  F1: 0.0676
Category: 3
  Precision: 0.0000
  Recall: 0.0000
  F1: 0.0000
The average precision is: 0.2511
The average recall is: 0.2350
The average f1 is: 0.2368
  Testing took: 0:00:28
